# 이거 kor nli로 바꿔야댐

# HuggingFace Transformers를 활용한 문장 분류 모델 학습

본 노트북에서는 `klue/roberta-base` 모델을 **KLUE** 내 **NLI** 데이터셋을 활용하여 모델을 훈련하는 예제를 다루게 됩니다.

학습을 통해 얻어질 `klue-roberta-base-nli` 모델은 입력된 두 문장의 추론 관계를 예측하는데 사용할 수 있게 됩니다.

학습 과정 이후에는 간단한 예제 코드를 통해 모델이 어떻게 활용되는지도 함께 알아보도록 할 것입니다.

모든 소스 코드는 [`huggingface-notebooks`](https://github.com/huggingface/notebooks)를 참고하였습니다.

먼저, 노트북을 실행하는데 필요한 라이브러리를 설치합니다. 모델 훈련을 위해서는 `transformers`가, 학습 데이터셋 로드를 위해서는 `datasets` 라이브러리의 설치가 필요합니다. 그 외 모델 성능 검증을 위해 `scipy`, `scikit-learn`을 추가로 설치해주도록 합니다.

In [1]:
 !pip install -U transformers datasets scipy accelerate # 재시작 하기

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.2/7.2 MB 106.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 485.6/485.6 kB 52.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 227.6/227.6 kB 27.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 236.8/236.8 kB 33.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 106.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 87.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.5/110.5 kB 17.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.5/212.5 kB 31.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.3/134.3 kB 22.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 86.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 114.5/114.5 kB 14.7 MB/s eta 0:00:00
     ━━━━━━━━━━━

## 문장 분류 모델 학습

노트북을 실행하는데 필요한 라이브러리들을 모두 임포트합니다.

In [1]:
import random
import logging
from IPython.display import display, HTML

import numpy as np
import pandas as pd
import datasets
from datasets import load_dataset, load_metric, ClassLabel, Sequence, concatenate_datasets
from transformers import AutoTokenizer, AutoModelForSequenceClassification, TrainingArguments, Trainer

학습에 필요한 정보를 변수로 기록합니다.

본 노트북에서는 `klue-roberta-base` 모델을 활용하지만, https://huggingface.co/klue 페이지에서 더 다양한 사전학습 언어 모델을 확인하실 수 있습니다.

학습 태스크로는 `nli`를, 배치 사이즈로는 32를 지정하겠습니다.

In [2]:
model_checkpoint = "klue/roberta-base"
batch_size = 32

이제 HuggingFace `datasets` 라이브러리에 등록된 KLUE 데이터셋 중, NLI 데이터를 내려받습니다.

In [3]:
datasets1 = load_dataset("kor_nli",'multi_nli')
datasets2 = load_dataset("kor_nli",'snli')
datasets3 = load_dataset("kor_nli",'xnli')

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/2 [00:00<?, ?it/s]

학습이 너무 오래결려서 반으로 줄인다...

In [4]:
#datasets = concatenate_datasets([datasets1['train'], datasets2['train']])
#datasets = concatenate_datasets([datasets, datasets3['validation']])
#datasets = concatenate_datasets([datasets, datasets3['test']])
#datasets = datasets.train_test_split(test_size=0.1)
#datasets

datasets = concatenate_datasets([datasets1['train'], datasets3['validation']])
datasets = concatenate_datasets([datasets, datasets3['test']])
datasets = datasets.train_test_split(test_size=0.1)
datasets

DatasetDict({
    train: Dataset({
        features: ['premise', 'hypothesis', 'label'],
        num_rows: 360181
    })
    test: Dataset({
        features: ['premise', 'hypothesis', 'label'],
        num_rows: 40021
    })
})

각 예시 데이터는 아래와 같이 두 개의 문장과 두 문장의 추론 관계를 라벨로 지니고 있습니다.

In [5]:
datasets["train"][0]

{'premise': '스페인에서 가장 인기 있는 종교 예술가인 바르톨로모 무릴로(1617 1682년)는 존경받는 성서적 성격을 편안하게 묘사했다.',
 'hypothesis': '바르톨로모 무릴로는 성서적 성격을 묘사하지 않는 것을 선호했다.',
 'label': 2}

데이터셋을 전반적으로 살펴보기 위한 시각화 함수를 다음과 같이 정의합니다.

In [6]:
def show_random_elements(dataset, num_examples=10):
    assert num_examples <= len(dataset), "Can't pick more elements than there are in the dataset."

    picks = []

    for _ in range(num_examples):
        pick = random.randint(0, len(dataset)-1)

        # 이미 등록된 예제가 뽑힌 경우, 다시 추출
        while pick in picks:
            pick = random.randint(0, len(dataset)-1)

        picks.append(pick)

    # 임의로 추출된 인덱스들로 구성된 데이터 프레임 선언
    df = pd.DataFrame(dataset[picks])

    for column, typ in dataset.features.items():
        # 라벨 클래스를 스트링으로 변환
        if isinstance(typ, ClassLabel):
            df[column] = df[column].transform(lambda i: typ.names[i])

    display(HTML(df.to_html()))

앞서 정의한 함수를 활용해 훈련 데이터를 살펴보도록 합시다.

이처럼 데이터를 살펴보는 것의 장점으로는 각 라벨에 어떠한 문장들이 해당하는지에 대한 감을 익힐 수 있다는데에 있습니다.

**KLUE NLI**는 `entailment`, `neutral` 그리고 `contradiction` 세 개의 라벨을 지니는 데이터셋임을 확인할 수 있습니다.

In [7]:
show_random_elements(datasets["train"])

훈련 과정 중 모델의 성능을 파악하기 위한 메트릭을 설정합니다.

`datasets` 라이브러리에는 이미 구현된 메트릭을 사용할 수 있는 `load_metric` 함수가 있습니다.

그 중 **GLUE** 데이터셋에 이미 다양한 메트릭이 구현되어 있으므로, **GLUE** 그 중에서도 **KLUE NLI**와 동일한 `accuracy` 메트릭을 사용하는 `qnli` 태스크의 메트릭을 사용합니다.

In [8]:
metric = load_metric("glue", "qnli")

<ipython-input-8-4b8a033d74b0>:1: FutureWarning: load_metric is deprecated and will be removed in the next major version of datasets. Use 'evaluate.load' instead, from the new library 🤗 Evaluate: https://huggingface.co/docs/evaluate
  metric = load_metric("glue", "qnli")


`accuracy` 메트릭이 정상적으로 작동하는지 확인하기 위해, 랜덤한 예측 값과 라벨 값을 생성합니다.

In [9]:
fake_preds = np.random.randint(0, 2, size=(64,))
fake_labels = np.random.randint(0, 2, size=(64,))
fake_preds, fake_labels

(array([0, 1, 0, 1, 0, 0, 1, 0, 1, 0, 1, 0, 1, 0, 0, 1, 1, 1, 1, 0, 1, 0,
        0, 1, 1, 1, 0, 0, 1, 1, 1, 1, 0, 0, 1, 1, 0, 0, 1, 0, 1, 1, 0, 0,
        0, 0, 0, 1, 1, 1, 1, 1, 0, 0, 0, 1, 0, 0, 1, 1, 1, 1, 0, 0]),
 array([0, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 0, 0, 1, 1, 0, 0, 0, 0, 0, 0, 0,
        0, 1, 0, 1, 0, 1, 1, 0, 1, 1, 0, 1, 0, 1, 1, 0, 1, 1, 1, 1, 0, 0,
        1, 1, 0, 1, 1, 0, 1, 1, 0, 1, 0, 1, 0, 1, 0, 0, 1, 0, 1, 0]))

앞서 생성한 랜덤 예측, 랜덤 라벨 값을 `compute()` 함수에 입력해 잘 동작하는지 확인해봅시다.

In [10]:
metric.compute(predictions=fake_preds, references=fake_labels)

{'accuracy': 0.53125}

이제 학습에 활용할 토크나이저를 로드해오도록 합니다.

In [11]:
tokenizer = AutoTokenizer.from_pretrained(model_checkpoint, use_fast=True)

로드된 토크나이저가 두 개 문장을 토큰화하는 방식을 파악하기 위해 두 문장을 입력 값으로 넣어줘보도록 합시다.

In [12]:
tokenizer("남자가 공구 상자를 인도 아래로 옮기고 있다.", "남자는 밖으로 걸어 나간다")

{'input_ids': [0, 3997, 2116, 11451, 7777, 2138, 4543, 4402, 2200, 7590, 2088, 1513, 2062, 18, 2, 3997, 2259, 1120, 6233, 5756, 11314, 2], 'token_type_ids': [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], 'attention_mask': [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]}

`input_ids`를 보시면 `cls_token`에 해당하는 2번 토큰이 가장 좌측에 붙게 되며, `sep_token`의 3번 토큰이 각각 중간과 가장 우측에 더해진 것을 확인할 수 있습니다.

이제 앞서 로드한 데이터셋에서 각 문장에 해당하는 *value* 를 뽑아주기 위한 *key* 를 정의합니다.

앞서 **KLUE NLI** 데이터셋의 두 문장은 각각 `premise`와 `hypothesis`라는 이름으로 정의된 것을 확인하였으니, 두 문장의 *key* 는 마찬가지로 각각 `premise`, `hypothesis`가 되게 됩니다.

In [13]:
sentence1_key, sentence2_key = ("premise", "hypothesis")
print(f"Sentence 1: {datasets['train'][0][sentence1_key]}")
print(f"Sentence 2: {datasets['train'][0][sentence2_key]}")

Sentence 1: 스페인에서 가장 인기 있는 종교 예술가인 바르톨로모 무릴로(1617 1682년)는 존경받는 성서적 성격을 편안하게 묘사했다.
Sentence 2: 바르톨로모 무릴로는 성서적 성격을 묘사하지 않는 것을 선호했다.


이제 *key* 도 확인이 되었으니, 데이터셋에서 각 예제들을 뽑아와 토큰화 할 수 있는 함수를 아래와 같이 정의해줍니다.

해당 함수는 모델을 훈련하기 앞서 데이터셋을 미리 토큰화 시켜놓는 작업을 위한 콜백 함수로 사용되게 됩니다.

인자로 넣어주는 `truncation`는 모델이 입력 받을 수 있는 최대 길이 이상의 토큰 시퀀스가 들어오게 될 경우, 최대 길이 기준으로 시퀀스를 자르라는 의미를 지닙니다.

( \* `return_token_type_ids`는 토크나이저가 `token_type_ids`를 반환하도록 할 것인지를 결정하는 인자입니다. `transformers==4.7.0` 기준으로 `token_type_ids`가 기본적으로 반환되므로 `token_type_ids` 자체를 사용하지 않는 `RoBERTa` 모델을 활용하기 위해 해당 인자를 `False`로 설정해주도록 합니다.)

In [14]:
def preprocess_function(examples):
    return tokenizer(
        examples[sentence1_key],
        examples[sentence2_key],
        truncation=True,
        return_token_type_ids=False,
    )

앞서 정의한 `process_function`은 여러 개의 예제 데이터를 받을 수도 있습니다.

In [15]:
preprocess_function(datasets["train"][:5])

{'input_ids': [[0, 6385, 27135, 3676, 4316, 1513, 2259, 4786, 8560, 2179, 5957, 2777, 2200, 2391, 1088, 2388, 2200, 12, 16956, 2254, 16713, 2302, 2440, 13, 793, 7534, 2757, 2259, 8344, 2125, 4768, 2069, 5984, 2205, 2318, 6885, 2371, 2062, 18, 2, 5957, 2777, 2200, 2391, 1088, 2388, 2200, 2259, 8344, 2125, 4768, 2069, 6885, 2205, 2118, 1380, 2259, 575, 2069, 5877, 2371, 2062, 18, 2], [0, 831, 29584, 2088, 8331, 2170, 2259, 19786, 2052, 1513, 2359, 2062, 18, 2, 831, 29584, 2088, 8331, 2170, 2259, 19786, 2052, 1513, 2359, 2062, 18, 2], [0, 7032, 25657, 2155, 2079, 4132, 4471, 2252, 2052, 2359, 2414, 3752, 12489, 2179, 4075, 2259, 1750, 2318, 1567, 2359, 2062, 18, 2, 25657, 2155, 2170, 2259, 636, 3875, 904, 2178, 2062, 2119, 1039, 2073, 10290, 2116, 1513, 2062, 18, 2], [0, 1439, 2138, 3685, 16, 3698, 2073, 4426, 3759, 4076, 2069, 9962, 4897, 2200, 1238, 2886, 2088, 3659, 2079, 17600, 2170, 3618, 14544, 2502, 4192, 2069, 1410, 2015, 3694, 4071, 2138, 5651, 2371, 2062, 18, 2, 3698, 2073, 3659

이제 정의된 전처리 함수를 활용해 데이터셋을 미리 토큰화시키는 작업을 수행합니다.

`datasets` 라이브러리를 통해 얻어진 `DatasetDict` 객체는 `map()` 함수를 지원하므로, 정의된 전처리 함수를 데이터셋 토큰화를 위한 콜백 함수로 `map()` 함수 인자로 넘겨주면 됩니다.

보다 자세한 내용은 [문서](https://huggingface.co/docs/datasets/processing.html#processing-data-with-map)를 참조해주시면 됩니다.

In [16]:
encoded_datasets = datasets.map(preprocess_function, batched=True)

Map:   0%|          | 0/360181 [00:00<?, ? examples/s]

Map:   0%|          | 0/40021 [00:00<?, ? examples/s]

학습을 위한 모델을 로드할 차례입니다.

앞서 살펴본 바와 같이 **KLUE NLI**에는 총 3개의 클래스가 존재하므로, 3개의 클래스를 예측할 수 있는 *SequenceClassification* 구조로 모델을 로드하도록 합니다.

In [17]:
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:
  print('Not connected to a GPU')
else:
  print(gpu_info)

Thu Jun 22 00:13:26 2023       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 525.85.12    Driver Version: 525.85.12    CUDA Version: 12.0     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  NVIDIA A100-SXM...  Off  | 00000000:00:04.0 Off |                    0 |
| N/A   30C    P0    42W / 400W |      0MiB / 40960MiB |      0%      Default |
|                               |                      |             Disabled |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [18]:
num_labels = 3
model = AutoModelForSequenceClassification.from_pretrained(model_checkpoint, num_labels=num_labels)

Some weights of the model checkpoint at klue/roberta-base were not used when initializing RobertaForSequenceClassification: ['lm_head.layer_norm.bias', 'lm_head.dense.bias', 'lm_head.layer_norm.weight', 'lm_head.bias', 'lm_head.dense.weight']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at klue/roberta-base and are newly initialized: ['classifier.out_proj.weight', 'classifier.dense.weight', 'classifier.dense.bias', 'classifier.out_proj.bias']
You

모델을 로드할 때 발생하는 경고 문구는 두 가지 의미를 지닙니다.

1. *Masked Language Modeling* 을 위해 존재했던 `lm_head`가 현재는 사용되지 않고 있음을 의미합니다.
2. 문장 분류를 위한 `classifier` 레이어를 백본 모델 뒤에 이어 붙였으나 아직 훈련이 되지 않았으므로, 학습을 수행해야 함을 의미합니다.

마지막으로 앞서 정의한 메트릭을 모델 예측 결과에 적용하기 위한 함수를 정의합니다.

입력으로 들어오는 `eval_pred`는 [*EvalPrediction*](https://huggingface.co/transformers/internal/trainer_utils.html#transformers.EvalPrediction) 객체이며, 모델의 클래스 별 예측 값과 정답 값을 지닙니다.

클래스 별 예측 중 가장 높은 라벨을 `argmax()`를 통해 뽑아낸 후, 정답 라벨과 비교를 하게 됩니다.

In [19]:
def compute_metrics(eval_pred):
    predictions, labels = eval_pred
    predictions = np.argmax(predictions, axis=1)
    return metric.compute(predictions=predictions, references=labels)

이제 앞서 정의한 정보들을 바탕으로 `transformers`에서 제공하는 *Trainer* 객체를 활용하기 위한 인자 관리 클래스를 초기화합니다.

`metric_name`은 앞서 얻어진 메트릭 함수를 활용했을 때, 아래와 같이 `dict` 형식으로 결과 값이 반환되는데 여기서 우리가 사용할 *key* 를 정의해준다고 생각하시면 됩니다.

```python
>>> metric.compute(predictions=fake_preds, references=fake_labels)
{'accuracy': 0.515625}
```

각 인자에 대한 자세한 설명은 [문서](https://huggingface.co/transformers/main_classes/trainer.html#trainingarguments)에서 참조해주시면 됩니다.

In [20]:
metric_name = "accuracy"

args = TrainingArguments(
    "test-nli",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=5,
    weight_decay=0.01,
    load_best_model_at_end=False,
    save_strategy="epoch",
    save_total_limit = 10,
    metric_for_best_model=metric_name,
)

이제 로드한 모델, 인자 관리 클래스, 데이터셋 등을 *Trainer* 클래스를 초기화에 넘겨주도록 합니다.

(TIP: Q: 이미 `encoded_datasets`을 만드는 과정에 토큰화가 이루어졌는데 토크나이저를 굳이 넘겨주는 이유가 무엇인가요?,<br>A: 토큰화는 이루어졌지만 학습 과정 시, 데이터를 배치 단위로 넘겨주는 과정에서 배치에 포함된 가장 긴 시퀀스 기준으로 `truncation`을 수행하고 최대 길이 시퀀스 보다 짧은 시퀀스들은 그 길이만큼 `padding`을 수행해주기 위함입니다.)

In [21]:
trainer = Trainer(
    model,
    args,
    train_dataset=encoded_datasets["train"],
    eval_dataset=encoded_datasets["test"],
    tokenizer=tokenizer,
    compute_metrics=compute_metrics,
)

이제 정의된 *Trainer* 객체를 다음과 같이 훈련시킬 수 있습니다.

에폭이 지남에 따라 *Loss* 는 떨어지고, 앞서 선정한 메트릭인 *Accuracy* 는 증가하는 것을 확인할 수 있습니다.

In [22]:
trainer.train()

/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
You're using a BertTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


TrainOutput(global_step=56280, training_loss=0.3434749272501714, metrics={'train_runtime': 8631.4556, 'train_samples_per_second': 208.644, 'train_steps_per_second': 6.52, 'total_flos': 9.673161506543254e+16, 'train_loss': 0.3434749272501714, 'epoch': 5.0})

*Trainer* 는 학습을 마치게 되면, `load_best_model_at_end=True` 인자에 따라 메트릭 기준 가장 좋은 성능을 보였던 체크포인트를 로드하게 됩니다.

본 노트북에서는 마지막 에폭 때 가장 좋은 성능을 얻었기에 `evaluate`를 수행해도 같은 결과가 나오겠습니다.

In [23]:
trainer.evaluate()

{'eval_loss': 0.7363672256469727,
 'eval_accuracy': 0.8114240023987407,
 'eval_runtime': 57.0187,
 'eval_samples_per_second': 701.892,
 'eval_steps_per_second': 21.94,
 'epoch': 5.0}

In [25]:
!pip install huggingface_hub

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [26]:
from huggingface_hub import notebook_login

notebook_login()

In [27]:
from huggingface_hub import create_repo
repo_name = "pongjin/roberta_with_kornli"
create_repo(repo_name)

RepoUrl('https://huggingface.co/pongjin/roberta_with_kornli', endpoint='https://huggingface.co', repo_type='model', repo_id='pongjin/roberta_with_kornli')

In [31]:
trainer.push_to_hub('pongjin/test-nli')

╭─────────────────────────────── Traceback (most recent call last) ────────────────────────────────╮
│ in <cell line: 1>:1                                                                              │
│                                                                                                  │
│ /usr/local/lib/python3.10/dist-packages/transformers/trainer.py:3716 in push_to_hub              │
│                                                                                                  │
│   3713 │   │   # If a user calls manually `push_to_hub` with `self.args.push_to_hub = False`, w  │
│   3714 │   │   # it might fail.                                                                  │
│   3715 │   │   if not hasattr(self, "repo"):                                                     │
│ ❱ 3716 │   │   │   self.init_git_repo()                                                          │
│   3717 │   │                                                                                     │
│   3718 │   │   model_name = kwargs.pop("model_name", None)                                       │
│   3719 │   │   if model_name is None and self.args.should_save:                                  │
│                                                                                                  │
│ /usr/local/lib/python3.10/dist-packages/transformers/trainer.py:3571 in init_git_repo            │
│                                                                                                  │
│   3568 │   │   # Make sure the repo exists.                                                      │
│   3569 │   │   create_repo(repo_name, token=self.args.hub_token, private=self.args.hub_private_  │
│   3570 │   │   try:                                                                              │
│ ❱ 3571 │   │   │   self.repo = Repository(self.args.output_dir, clone_from=repo_name, token=sel  │
│   3572 │   │   except EnvironmentError:                                                          │
│   3573 │   │   │   if self.args.overwrite_output_dir and at_init:                                │
│   3574 │   │   │   │   # Try again after wiping output_dir                                       │
│                                                                                                  │
│ /usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_validators.py:118 in _inner_fn    │
│                                                                                                  │
│   115 │   │   if check_use_auth_token:                                                           │
│   116 │   │   │   kwargs = smoothly_deprecate_use_auth_token(fn_name=fn.__name__, has_token=ha   │
│   117 │   │                                                                                      │
│ ❱ 118 │   │   return fn(*args, **kwargs)                                                         │
│   119 │                                                                                          │
│   120 │   return _inner_fn  # type: ignore                                                       │
│   121                                                                                            │
│                                                                                                  │
│ /usr/local/lib/python3.10/dist-packages/huggingface_hub/repository.py:516 in __init__            │
│                                                                                                  │
│    513 │   │   │   self.huggingface_token = HfFolder.get_token()                                 │
│    514 │   │                                                                                     │
│    515 │   │   if clone_from is not None:                                                        │
│ ❱  516 │   │   │   self.clone_from(repo_url=clone_from)                                          │
│    517 │   │   else:                                       

In [29]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [30]:
# push to hub는 에러가 뜨기에 직접 코랩 로컬에 저장 후 다운로드
trainer.save_model("/content/drive/MyDrive/국민은행과제")

지금까지 `transformers`를 라이브러리 내 문장 분류 모델을 학습하는 과정을 KLUE NLI 데이터셋을 통해 알아보았습니다.

본 노트북을 통해 습득한 지식이 여러분의 업무와 학습에 도움이 되었으면 좋겠습니다.

```
허 훈 (huffonism@gmail.com)
```

APPENDIX: 앞서 학습된 모델을 HuggingFace 모델 허브에 업로드하였으니, 아래 예제와 같이 `pipeline` 함수를 통해 사용이 가능합니다.

먼저 `text-classification` 태스크로 파이프라인 객체를 초기화합니다.

( \* `return_all_scores`는 모델이 입력 문장에 대해 측정한 각 라벨에 대한 확률 값을 모두 보여줄 것인지를 결정하는 인자입니다.)

In [ ]:
from transformers import pipeline

classifier = pipeline(
    "text-classification",
    model="Huffon/klue-roberta-base-nli",
    return_all_scores=True,
)

NLI는 두 문장의 페어를 입력 값으로 주어야 하기 때문에 구분자 스페셜 토큰을 두 문장 사이에 넣어주기 위해 토크나이저 객체를 로드합니다.

`[SEP]` 문자열을 하드코딩하여 넣어줄 수도 있겠지만, 스페셜 토큰은 토크나이저 마다 다르게 정의되므로 다른 모델을 활용할 때 보다 코드를 재사용할 수 있도록 토크나이저의 `sep_token` 프로퍼티에 접근하는 방식으로 코드를 작성합니다.

In [ ]:
tokenizer = AutoTokenizer.from_pretrained("Huffon/klue-roberta-base-nli")

In [ ]:
tokenizer.sep_token

'[SEP]'

`sep_token`으로 두 문장을 이어 하나의 입력 값으로 파이프라인에 넘겨줍니다.

입력된 문장에 대해 모델이 각 라벨에 대해 어떤 확률을 가지고 예측했는지를 확인할 수 있습니다.

In [ ]:
classifier(f"흡연하려면 발코니 있는 방을 선택하면 됩니다. {tokenizer.sep_token} 흡연자분들은 발코니가 있는 방이면 발코니에서 흡연이 가능합니다.")

[[{'label': 'ENTAILMENT', 'score': 0.9865273833274841},
  {'label': 'NEUTRAL', 'score': 0.013215206563472748},
  {'label': 'CONTRADICTION', 'score': 0.0002573762903921306}]]

In [ ]:
classifier(f"호스트분은 영어밖에 못하십니다. {tokenizer.sep_token} 호스트분도 엄청 친절하시고 영어도 잘하십니다.")

[[{'label': 'ENTAILMENT', 'score': 0.0002685467479750514},
  {'label': 'NEUTRAL', 'score': 0.0006742384284734726},
  {'label': 'CONTRADICTION', 'score': 0.9990572333335876}]]

검증 데이터에 존재하는 임의의 문장 페어를 입력해보니, 우리가 원하던 결과를 얻을 수 있었습니다.

*(cf. NLI 데이터에 대해 학습된 모델을 활용해 Zero-shot Classification을 수행하는 예제가 궁금하신 분들은 해당 [노트북](https://colab.research.google.com/github/Huffon/klue-transformers-tutorial/blob/master/zero_shot_classification.ipynb)을 참조해주세요.)*